In [129]:
from model_builder import ModelBuilder
from sklearn.linear_model import Lasso, Ridge, LassoCV, RidgeCV
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import json
import os
from model_utils import *
import scipy.stats as stats 

## Multi-Task Modeling Playground

The goal of this notebook is to prototype the modeling process for the team ingredient horse race project on the multi-task data.

For *each task* ...

We want to understand the effect of different "ingredients of a team" (Composition, Task, and Conversation) on its ultimate performance.

Team Composition:
- ['birth_year', 'CRT', 'income_max', 'income_min', 'IRCS_GS', 'IRCS_GV', 'IRCS_IB', 'IRCS_IR', 'IRCS_IV', 'IRCS_RS', 'political_fiscal', 'political_social', 'RME', 'country', 'education_level', 'gender', 'marital_status', 'political_party', 'race']
- Number of players: 'playerCount'

Task Features:
- Need to append from the Task Map
- ['complexity', 'task']

Conversation Features (All)
- Everything else that is NOT an ID or a dependent variable

# Read and Preprocess Data
The function below reads in the dataframe and preprocesses each group of features:

- Composition
- Task
- Conversation

And also parses out the possible dependent variables.

In [130]:
def drop_invariant_columns(df):
    """
    Certain features are invariant throughout the training data (e.g., the entire column is 0 throughout).

    These feature obviously won't be very useful predictors, so we drop them.
    
    This function works by identifying columns that only have 1 unique value throughout the entire column,
    and then dropping them.

    @df: the dataframe containing the features (this should be X).
    """
    nunique = df.nunique()
    cols_to_drop = nunique[nunique == 1].index
    return(df.drop(cols_to_drop, axis=1))


In [131]:
def read_and_preprocess_data(path, min_num_chats):
    conv_data  = pd.read_csv(path)

    # Filter this down to teams that have at least min_num of chats
    # Can also comment this out to re-run results on *all* conversations!
    conv_data = conv_data[conv_data["sum_num_messages"] >= min_num_chats]


    # Save the important information

    # DV
    dvs = conv_data[["score","speed","efficiency","raw_duration_min","default_duration_min"]]

    # Team Composition
    composition_colnames = ['birth_year', 'CRT', 'income_max', 'income_min', 'IRCS_GS', 'IRCS_GV', 'IRCS_IB', 'IRCS_IR',
                'IRCS_IV', 'IRCS_RS', 'political_fiscal', 'political_social', 'RME', 'country', 'education_level',
                'gender', 'marital_status', 'political_party', 'race', 'playerCount']
    
    # Select columns that contain the specified keywords
    composition = conv_data[[col for col in conv_data.columns if any(keyword in col for keyword in composition_colnames)]]

    # Task
    task = conv_data[['task', 'complexity']].copy()

    task_map_path = '../utils/task_map.csv' # get task map
    task_map = pd.read_csv(task_map_path)

    task_name_mapping = {
        "Moral Reasoning": "Moral Reasoning (Disciplinary Action Case)",
        "Wolf Goat Cabbage": "Wolf, goat and cabbage transfer",
        "Guess the Correlation": "Guessing the correlation",
        "Writing Story": "Writing story",
        "Room Assignment": "Room assignment task",
        "Allocating Resources": "Allocating resources to programs",
        "Divergent Association": "Divergent Association Task",
        "Word Construction": "Word construction from a subset of letters",
        "Whac a Mole": "Whac-A-Mole"
    }
    task.loc[:, 'task'] = task['task'].replace(task_name_mapping)
    task = pd.merge(left=task, right=task_map, on = "task", how='left')
    
    # Create dummy columns for 'complexity'
    complexity_dummies = pd.get_dummies(task['complexity'])
    task = pd.concat([task, complexity_dummies], axis=1)   
    task.drop(['complexity', 'task'], axis=1, inplace=True)

    # Conversation
    conversation = conv_data.drop(columns=list(dvs.columns) + list(composition.columns) + ['task', 'complexity', 'stageId', 'roundId', 'cumulative_stageId', 'gameId', 'message', 'message_lower_with_punc', 'speaker_nickname', 'conversation_num', 'timestamp'])
    conversation = drop_invariant_columns(conversation) # drop invariant conv features

    return composition, task, conversation, dvs

In [132]:
tiny_multitask = 'conv/multi_task_TINY_output_conversation_level_stageId_cumulative.csv'
multitask_cumulative_by_stage = 'conv/multi_task_output_conversation_level_stageId_cumulative.csv'
multitask_cumulative_by_stage_and_task = 'conv/multi_task_output_conversation_level_stageId_cumulative_within_task.csv'

In [133]:
# PARAMETERS
min_num_chats = 0
desired_target = "score"
data_path = "../output/"
output_path = "./results/multi_task_cumulative_stage/" + "min=" + str(min_num_chats) + "/" + desired_target + "/"
validation_results_output_name = output_path + "multi_task_lasso_ridge_experiments" + "_" + desired_target + "_min_chat_num_" + str(min_num_chats) + ".csv"

In [134]:
team_composition_features, task_features, conv_features, targets = read_and_preprocess_data(data_path + multitask_cumulative_by_stage, min_num_chats=min_num_chats)

# Number of points in dataset
len(conv_features)

1018

# Set up X's and y's

In [135]:
X_train = pd.concat([team_composition_features, task_features, conv_features], axis = 1)
X_train = X_train.fillna(-1) # TODO --- need a better way to handle NA's!
y_train = targets

## Try LASSO/Ridge Regression, one Set of Features at a Time

Here, we want to implement *leave-one-out cross-validation*, and use Q^2 as our metric.



In [136]:
# Note --- this uses k-fold cross-validation with k = 5 (the default)
# We are testing 10,000 different alphas, so I feel like this is an OK heuristic
def get_optimal_alpha(y_target, feature_columns_list, lasso):

    if(lasso == True):
        model = LassoCV(n_alphas = 10000)
        model.fit(X_train[feature_columns_list], y_train[y_target])
    else:
        model = RidgeCV(n_alphas = 10000)
        model.fit(X_train[feature_columns_list], y_train[y_target])
        
    return model.alpha_ # optimal alpha

In [137]:
def fit_regularized_linear_model(y_target, feature_columns_list, lasso=True, tune_alpha=False):

    if not tune_alpha:
        alpha = 1.0
    else:
        # Hyperparameter tune the alpha
        alpha = get_optimal_alpha(y_target, feature_columns_list, lasso=True)

    if lasso:
        model = Lasso(alpha=alpha)
    else:
        model = Ridge(alpha=alpha)

    # Calculation of Q^2 metric
    squared_model_prediction_errors = []
    squared_average_prediction_errors = []

    # Initialize a list to store coefficients
    coefficients_list = []

    # Leave one out -- iterate through the entire length of the dataset
    for i in range(len(y_train)):
        # Store the evaluation datapoint
        evaluation_X = X_train.iloc[[i]]
        evaluation_y = y_train.iloc[[i]][y_target]

        # Drop the ith datapoint (leave this one out)
        X_train_fold = X_train.drop(X_train.index[i])
        y_train_fold = y_train.drop(y_train.index[i])[y_target]

        # Fit the model
        model.fit(X_train_fold[feature_columns_list], y_train_fold)

        # Save the Prediction Error
        prediction = model.predict(evaluation_X[feature_columns_list])[0]
        squared_model_prediction_errors.append((evaluation_y - prediction) ** 2)

        # Save the Total Error for this fold
        squared_average_prediction_errors.append((evaluation_y - np.mean(y_train_fold)) ** 2)

        # Append the coefficients to the list
        coefficients_list.append(model.coef_)

    # Create a DataFrame with feature names as rows and iteration results as columns
    feature_coefficients = pd.DataFrame(coefficients_list, columns=feature_columns_list).T

    q_squared = 1 - (np.sum(squared_model_prediction_errors) / np.sum(squared_average_prediction_errors))
    print("Q^2: " + str(q_squared))

    return model, q_squared, feature_coefficients


In [138]:
def display_feature_coefficients(feature_coef_df):
    # Initialize a list to store DataFrames for each feature
    dfs = []

    # Iterate through the rows of the input DataFrame
    for feature_name, coefficients in feature_coef_df.iterrows():
        # Calculate the confidence interval without NaN values
        non_nan_coefficients = coefficients[~np.isnan(coefficients)]
        if len(non_nan_coefficients) == 0:
            # Handle the case where there are no valid coefficients
            continue

        mean_coef = non_nan_coefficients.mean()

        # Check if all coefficients in the row are the same
        if len(coefficients.unique()) == 1:
            # If all coefficients are the same, set the lower and upper CI to the mean
            confidence_interval = (mean_coef, mean_coef)
        else:
            std_error = non_nan_coefficients.sem()
            confidence_interval = stats.t.interval(0.95, len(non_nan_coefficients) - 1, loc=mean_coef, scale=std_error)

        # Create a DataFrame for the summary data
        temp_df = pd.DataFrame({
            "Feature": [feature_name],
            "Mean": [mean_coef],
            "Lower_CI": [confidence_interval[0]],
            "Upper_CI": [confidence_interval[1]]
        })

        # Append the temporary DataFrame to the list
        dfs.append(temp_df)

    # Concatenate all the DataFrames in the list into the final summary DataFrame
    summary_df = pd.concat(dfs, ignore_index=True)

    return summary_df

In [139]:
def sort_by_mean_abs(df):
    return df.reindex(df["Mean"].abs().sort_values(ascending=False).index)

In [140]:
# Go through the different types of features and fit models

# First, create a data structure that saves the result
result = {
    "model": [],
    "model_type": [],
    "features_included": [],
    "alpha": [],
    "q_squared": []
}

result_df = pd.DataFrame(result)

## Team composition features

In [141]:
model_ridge_composition, mrc_q2, mrc_feature_coefficients = fit_regularized_linear_model(desired_target, team_composition_features.columns, lasso = False, tune_alpha = True)

result_df = pd.concat([result_df, pd.DataFrame({"model": [model_ridge_composition], "model_type": ["Ridge"], "features_included": ["Team Composition"], "alpha": [model_ridge_composition.alpha.round(4)], "q_squared": [mrc_q2]})], ignore_index=True)

Q^2: 0.02712302800183075


In [142]:
directory = os.path.dirname(output_path + 'mrc_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mrc_feature_coefficients.to_csv(output_path + 'mrc_feature_coefficients' + '.csv')

In [143]:
sort_by_mean_abs(display_feature_coefficients(mrc_feature_coefficients))

Feature      Mean  Lower_CI  Upper_CI
15               RME_nanmean  0.115979  0.115912  0.116046
0                playerCount  0.051623  0.051576  0.051670
7            IRCS_IB_nanmean -0.046278 -0.046289 -0.046267
16                RME_nanstd -0.045680 -0.045745 -0.045615
3            IRCS_GS_nanmean -0.025561 -0.025573 -0.025549
9            IRCS_IR_nanmean -0.025179 -0.025198 -0.025159
12            IRCS_IV_nanstd -0.024909 -0.024924 -0.024894
14            IRCS_RS_nanstd  0.018627  0.018615  0.018639
10            IRCS_IR_nanstd -0.017992 -0.018009 -0.017975
1                CRT_nanmean  0.017992  0.017986  0.017997
19            gender_nanmean -0.017212 -0.017221 -0.017203
29   political_party_nanmean -0.015118 -0.015131 -0.015104
18         birth_year_nanstd -0.014991 -0.015005 -0.014976
31  political_social_nanmean -0.010631 -0.010635 -0.010628
5            IRCS_GV_nanmean  0.010433  0.010417  0.010450
25    marital_status_nanmean -0.009265 -0.009277 -0.009253
27  political_fiscal_nanmean -0.007791 -0.007794 -0.007787
6             IRCS_GV_nanstd  0.006337  0.006325  0.006350
13           IRCS_RS_nanmean  0.005925  0.005909  0.005941
20             gender_nanstd  0.005509  0.005501  0.005517
30    political_party_nanstd  0.004612  0.004599  0.004625
26     marital_status_nanstd  0.004159  0.004148  0.004170
17        birth_year_nanmean -0.004146 -0.004157 -0.004135
11           IRCS_IV_nanmean -0.002949 -0.002979 -0.002920
28   political_fiscal_nanstd  0.002886  0.002882  0.002889
8             IRCS_IB_nanstd  0.002346  0.002333  0.002359
4             IRCS_GS_nanstd -0.000608 -0.000619 -0.000598
32   political_social_nanstd -0.000493 -0.000497 -0.000490
2                 CRT_nanstd  0.000279  0.000274  0.000283
23        income_min_nanmean  0.000168  0.000168  0.000168
24         income_min_nanstd  0.000097  0.000097  0.000097
22         income_max_nanstd -0.000057 -0.000057 -0.000056
21        income_max_nanmean -0.000004 -0.000004 -0.000004

In [144]:
model_lasso_composition, mlc_q2, mlc_feature_coefficients = fit_regularized_linear_model(desired_target, team_composition_features.columns, lasso = True, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_lasso_composition], "model_type": ["Lasso"], "features_included": ["Team Composition"], "alpha": [model_lasso_composition.alpha.round(4)], "q_squared": [mlc_q2]})], ignore_index=True)

Q^2: 0.020528274452905393


In [145]:
directory = os.path.dirname(output_path + 'mlc_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mlc_feature_coefficients.to_csv(output_path + 'mlc_feature_coefficients' + '.csv')

## Task Features

In [146]:
model_ridge_task, mrt_q2, mrt_feature_coefficients = fit_regularized_linear_model(desired_target, task_features.columns, lasso = False, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_ridge_task], "model_type": ["Ridge"], "features_included": ["Task Complexity"], "alpha": [model_ridge_task.alpha.round(4)], "q_squared": [mrt_q2]})], ignore_index=True)

Q^2: 0.2974385403380464


In [147]:
directory = os.path.dirname(output_path + 'mrt_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mrt_feature_coefficients.to_csv(output_path + 'mrt_feature_coefficients' + '.csv')

In [148]:
sort_by_mean_abs(display_feature_coefficients(mrt_feature_coefficients))

Feature       Mean   Lower_CI   Upper_CI
22    Q5creativity_input_1  46.729255  46.722419  46.736090
8            Q11optimizing  37.890786  37.878362  37.903210
19      Q24eureka_question -37.313419 -37.327911 -37.298928
13       Q17within_sys_sol -33.033407 -33.049286 -33.017528
6      Q9divisible_unitary -28.727838 -28.731864 -28.723812
1        Q3type_1_planning  26.523305  26.509832  26.536778
9        Q13outcome_multip  23.389089  23.384675  23.393503
3              Q6type_5_cc -18.509307 -18.516226 -18.502388
12     Q16shared_knowledge -16.902092 -16.903486 -16.900699
7            Q10maximizing -15.652993 -15.659460 -15.646525
10       Q14sol_scheme_mul -14.265451 -14.269035 -14.261867
4          Q7type_7_battle  13.815429  13.809609  13.821250
0          Q1concept_behav -12.526753 -12.531074 -12.522433
18        Q23ss_out_uncert -10.119131 -10.129084 -10.109179
21  Q21intellective_judg_1  -8.918309  -8.920465  -8.916153
15     Q19time_solvability   6.558447   6.555768   6.561126
17      Q22confl_tradeoffs  -5.858751  -5.864508  -5.852993
11    Q15dec_verifiability   5.578946   5.577287   5.580604
16        Q20type_3_type_4  -4.886381  -4.890302  -4.882460
2        Q4type_2_generate  -3.713571  -3.718591  -3.708551
26                  Medium  -3.171630  -3.173670  -3.169590
25                     Low   2.992589   2.990518   2.994661
14            Q18ans_recog   2.437840   2.435706   2.439974
5     Q8type_8_performance  -1.678412  -1.684838  -1.671986
20         Q2intel_manip_1   0.886248   0.880299   0.892197
24                    High   0.179041   0.177094   0.180987
23  Q25_type6_mixed_motive   0.000000   0.000000   0.000000

In [149]:
model_lasso_task, mlt_q2, mlt_feature_coefficients = fit_regularized_linear_model(desired_target, task_features.columns, lasso = True, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_lasso_task], "model_type": ["Lasso"], "features_included": ["Task Complexity"], "alpha": [model_lasso_task.alpha.round(4)], "q_squared": [mlt_q2]})], ignore_index=True)

Q^2: 0.28539737432670276


In [150]:
directory = os.path.dirname(output_path + 'mlt_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mlt_feature_coefficients.to_csv(output_path + 'mlt_feature_coefficients' + '.csv')

In [151]:
sort_by_mean_abs(display_feature_coefficients(mlt_feature_coefficients))

Feature       Mean   Lower_CI   Upper_CI
22    Q5creativity_input_1  61.444441  61.434393  61.454490
8            Q11optimizing  37.784589  37.766836  37.802343
6      Q9divisible_unitary -24.949892 -24.959929 -24.939855
19      Q24eureka_question -18.978516 -18.987495 -18.969536
7            Q10maximizing -15.402954 -15.409408 -15.396501
9        Q13outcome_multip   7.139211   7.121995   7.156426
26                  Medium  -2.966943  -2.970189  -2.963698
25                     Low   2.781520   2.778145   2.784894
16        Q20type_3_type_4   0.000000   0.000000   0.000000
24                    High   0.000000   0.000000   0.000000
23  Q25_type6_mixed_motive   0.000000   0.000000   0.000000
21  Q21intellective_judg_1   0.000000   0.000000   0.000000
20         Q2intel_manip_1   0.000000   0.000000   0.000000
18        Q23ss_out_uncert   0.000000   0.000000   0.000000
17      Q22confl_tradeoffs   0.000000   0.000000   0.000000
0          Q1concept_behav   0.000000   0.000000   0.000000
15     Q19time_solvability   0.000000   0.000000   0.000000
14            Q18ans_recog   0.000000   0.000000   0.000000
1        Q3type_1_planning   0.000000   0.000000   0.000000
12     Q16shared_knowledge   0.000000   0.000000   0.000000
11    Q15dec_verifiability   0.000000   0.000000   0.000000
10       Q14sol_scheme_mul   0.000000   0.000000   0.000000
5     Q8type_8_performance   0.000000   0.000000   0.000000
4          Q7type_7_battle   0.000000   0.000000   0.000000
3              Q6type_5_cc   0.000000   0.000000   0.000000
2        Q4type_2_generate   0.000000   0.000000   0.000000
13       Q17within_sys_sol   0.000000   0.000000   0.000000

## Task + Composition Together

In [152]:
task_comp_features = list(task_features.columns) + list(team_composition_features.columns)

model_ridge_taskcomp, mrtc_q2, mrtc_feature_coefficients = fit_regularized_linear_model(desired_target, task_comp_features, lasso = False, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_ridge_taskcomp], "model_type": ["Ridge"], "features_included": ["Team Composition + Task Complexity"], "alpha": [model_ridge_taskcomp.alpha.round(4)], "q_squared": [mrtc_q2]})], ignore_index=True)

Q^2: 0.027902022264065796


In [153]:
directory = os.path.dirname(output_path + 'mrtc_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mrtc_feature_coefficients.to_csv(output_path + 'mrtc_feature_coefficients' + '.csv')

In [154]:
sort_by_mean_abs(display_feature_coefficients(mrtc_feature_coefficients))

Feature      Mean  Lower_CI  Upper_CI
42               RME_nanmean  0.115778  0.115711  0.115845
27               playerCount  0.051607  0.051560  0.051654
34           IRCS_IB_nanmean -0.046242 -0.046253 -0.046231
43                RME_nanstd -0.045674 -0.045739 -0.045609
22      Q5creativity_input_1  0.037400  0.037392  0.037409
7              Q10maximizing -0.032724 -0.032734 -0.032713
6        Q9divisible_unitary -0.031151 -0.031158 -0.031143
25                       Low  0.028542  0.028525  0.028559
30           IRCS_GS_nanmean -0.025539 -0.025551 -0.025527
36           IRCS_IR_nanmean -0.025147 -0.025167 -0.025127
39            IRCS_IV_nanstd -0.024866 -0.024881 -0.024851
12       Q16shared_knowledge -0.020022 -0.020036 -0.020009
8              Q11optimizing  0.019891  0.019880  0.019903
41            IRCS_RS_nanstd  0.018600  0.018588  0.018612
19        Q24eureka_question  0.018098  0.018089  0.018108
28               CRT_nanmean  0.017991  0.017985  0.017996
37            IRCS_IR_nanstd -0.017962 -0.017979 -0.017945
46            gender_nanmean -0.017217 -0.017226 -0.017207
26                    Medium -0.017162 -0.017178 -0.017146
0            Q1concept_behav -0.015742 -0.015749 -0.015735
21    Q21intellective_judg_1 -0.015724 -0.015735 -0.015712
5       Q8type_8_performance  0.015501  0.015490  0.015512
56   political_party_nanmean -0.015118 -0.015132 -0.015105
45         birth_year_nanstd -0.015003 -0.015017 -0.014988
1          Q3type_1_planning  0.013527  0.013519  0.013535
3                Q6type_5_cc -0.012997 -0.013010 -0.012985
24                      High -0.011380 -0.011394 -0.011367
58  political_social_nanmean -0.010631 -0.010635 -0.010627
32           IRCS_GV_nanmean  0.010410  0.010393  0.010426
52    marital_status_nanmean -0.009266 -0.009278 -0.009254
10         Q14sol_scheme_mul -0.008890 -0.008898 -0.008883
17        Q22confl_tradeoffs -0.008757 -0.008770 -0.008744
20           Q2intel_manip_1 -0.008683 -0.008689 -0.008678
54  political_fiscal_nanmean -0.007791 -0.007794 -0.007787
33            IRCS_GV_nanstd  0.006326  0.006314  0.006339
40           IRCS_RS_nanmean  0.005905  0.005889  0.005921
47             gender_nanstd  0.005485  0.005477  0.005493
57    political_party_nanstd  0.004587  0.004574  0.004599
2          Q4type_2_generate -0.004495 -0.004505 -0.004485
44        birth_year_nanmean -0.004150 -0.004161 -0.004139
53     marital_status_nanstd  0.004131  0.004120  0.004142
9          Q13outcome_multip  0.004057  0.004045  0.004069
16          Q20type_3_type_4 -0.003624 -0.003637 -0.003611
38           IRCS_IV_nanmean -0.002931 -0.002961 -0.002902
55   political_fiscal_nanstd  0.002879  0.002875  0.002882
35            IRCS_IB_nanstd  0.002342  0.002329  0.002355
13         Q17within_sys_sol -0.001467 -0.001471 -0.001463
11      Q15dec_verifiability  0.001030  0.001017  0.001044
4            Q7type_7_battle -0.000946 -0.000949 -0.000943
31            IRCS_GS_nanstd -0.000607 -0.000618 -0.000597
59   political_social_nanstd -0.000498 -0.000502 -0.000495
18          Q23ss_out_uncert -0.000493 -0.000502 -0.000484
29                CRT_nanstd  0.000276  0.000272  0.000280
50        income_min_nanmean  0.000168  0.000168  0.000168
15       Q19time_solvability  0.000107  0.000095  0.000118
14              Q18ans_recog -0.000104 -0.000116 -0.000093
51         income_min_nanstd  0.000097  0.000097  0.000097
49         income_max_nanstd -0.000057 -0.000057 -0.000056
48        income_max_nanmean -0.000004 -0.000004 -0.000004
23    Q25_type6_mixed_motive  0.000000  0.000000  0.000000

In [155]:
model_lasso_taskcomp, mltc_q2, mltc_feature_coefficients = fit_regularized_linear_model(desired_target, task_comp_features, lasso = True, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_lasso_taskcomp], "model_type": ["Lasso"], "features_included": ["Team Composition + Task Complexity"], "alpha": [model_lasso_taskcomp.alpha.round(4)], "q_squared": [mltc_q2]})], ignore_index=True)

Q^2: 0.020528274452905393


In [156]:
directory = os.path.dirname(output_path + 'mltc_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mltc_feature_coefficients.to_csv(output_path + 'mltc_feature_coefficients' + '.csv')

In [157]:
sort_by_mean_abs(display_feature_coefficients(mltc_feature_coefficients))

Feature      Mean  Lower_CI  Upper_CI
50        income_min_nanmean  0.000105  0.000105  0.000105
0            Q1concept_behav  0.000000  0.000000  0.000000
44        birth_year_nanmean  0.000000  0.000000  0.000000
32           IRCS_GV_nanmean  0.000000  0.000000  0.000000
33            IRCS_GV_nanstd  0.000000  0.000000  0.000000
34           IRCS_IB_nanmean  0.000000  0.000000  0.000000
35            IRCS_IB_nanstd  0.000000  0.000000  0.000000
36           IRCS_IR_nanmean  0.000000  0.000000  0.000000
37            IRCS_IR_nanstd  0.000000  0.000000  0.000000
38           IRCS_IV_nanmean  0.000000  0.000000  0.000000
39            IRCS_IV_nanstd  0.000000  0.000000  0.000000
40           IRCS_RS_nanmean  0.000000  0.000000  0.000000
41            IRCS_RS_nanstd  0.000000  0.000000  0.000000
42               RME_nanmean  0.000000  0.000000  0.000000
43                RME_nanstd  0.000000  0.000000  0.000000
45         birth_year_nanstd  0.000000  0.000000  0.000000
1          Q3type_1_planning  0.000000  0.000000  0.000000
46            gender_nanmean  0.000000  0.000000  0.000000
47             gender_nanstd  0.000000  0.000000  0.000000
48        income_max_nanmean  0.000000  0.000000  0.000000
49         income_max_nanstd  0.000000  0.000000  0.000000
51         income_min_nanstd  0.000000  0.000000  0.000000
52    marital_status_nanmean  0.000000  0.000000  0.000000
53     marital_status_nanstd  0.000000  0.000000  0.000000
54  political_fiscal_nanmean  0.000000  0.000000  0.000000
55   political_fiscal_nanstd  0.000000  0.000000  0.000000
56   political_party_nanmean  0.000000  0.000000  0.000000
57    political_party_nanstd  0.000000  0.000000  0.000000
58  political_social_nanmean  0.000000  0.000000  0.000000
31            IRCS_GS_nanstd  0.000000  0.000000  0.000000
30           IRCS_GS_nanmean  0.000000  0.000000  0.000000
29                CRT_nanstd  0.000000  0.000000  0.000000
14              Q18ans_recog  0.000000  0.000000  0.000000
2          Q4type_2_generate  0.000000  0.000000  0.000000
3                Q6type_5_cc  0.000000  0.000000  0.000000
4            Q7type_7_battle  0.000000  0.000000  0.000000
5       Q8type_8_performance  0.000000  0.000000  0.000000
6        Q9divisible_unitary  0.000000  0.000000  0.000000
7              Q10maximizing  0.000000  0.000000  0.000000
8              Q11optimizing  0.000000  0.000000  0.000000
9          Q13outcome_multip  0.000000  0.000000  0.000000
10         Q14sol_scheme_mul  0.000000  0.000000  0.000000
11      Q15dec_verifiability  0.000000  0.000000  0.000000
12       Q16shared_knowledge  0.000000  0.000000  0.000000
13         Q17within_sys_sol  0.000000  0.000000  0.000000
15       Q19time_solvability  0.000000  0.000000  0.000000
28               CRT_nanmean  0.000000  0.000000  0.000000
16          Q20type_3_type_4  0.000000  0.000000  0.000000
17        Q22confl_tradeoffs  0.000000  0.000000  0.000000
18          Q23ss_out_uncert  0.000000  0.000000  0.000000
19        Q24eureka_question  0.000000  0.000000  0.000000
20           Q2intel_manip_1  0.000000  0.000000  0.000000
21    Q21intellective_judg_1  0.000000  0.000000  0.000000
22      Q5creativity_input_1  0.000000  0.000000  0.000000
23    Q25_type6_mixed_motive  0.000000  0.000000  0.000000
24                      High  0.000000  0.000000  0.000000
25                       Low  0.000000  0.000000  0.000000
26                    Medium  0.000000  0.000000  0.000000
27               playerCount  0.000000  0.000000  0.000000
59   political_social_nanstd  0.000000  0.000000  0.000000

## Conversation Alone

In [158]:
model_lasso_comms, mlcom_q2, mlcom_feature_coefficients = fit_regularized_linear_model(desired_target, conv_features.columns, lasso = True, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_lasso_comms], "model_type": ["Lasso"], "features_included": ["Communication"], "alpha": [model_lasso_comms.alpha.round(4)], "q_squared": [mlcom_q2]})], ignore_index=True)

Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.695e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.349e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.040e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.764e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.518e+02, tolerance: 6.381e+01
Objective did n

Q^2: -7.511795451020653e-05


In [159]:
directory = os.path.dirname(output_path + 'mlcom_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mlcom_feature_coefficients.to_csv(output_path + 'mlcom_feature_coefficients' + '.csv')

In [160]:
sort_by_mean_abs(display_feature_coefficients(mlcom_feature_coefficients))

Feature          Mean      Lower_CI  \
675              min_user_sum_time_diff -2.996172e-06 -3.004620e-06   
288                       max_time_diff -8.659169e-07 -8.675949e-07   
759   stdev_user_sum_certainty_rocklage  0.000000e+00  0.000000e+00   
760     min_user_sum_certainty_rocklage  0.000000e+00  0.000000e+00   
761     max_user_sum_certainty_rocklage  0.000000e+00  0.000000e+00   
...                                 ...           ...           ...   
390       average_user_sum_num_messages  0.000000e+00  0.000000e+00   
391         stdev_user_sum_num_messages  0.000000e+00  0.000000e+00   
392           min_user_sum_num_messages  0.000000e+00  0.000000e+00   
393           max_user_sum_num_messages  0.000000e+00  0.000000e+00   
1150               discursive_diversity  0.000000e+00  0.000000e+00   

          Upper_CI  
675  -2.987724e-06  
288  -8.642389e-07  
759   0.000000e+00  
760   0.000000e+00  
761   0.000000e+00  
...            ...  
390   0.000000e+00  
391   0.000000e+00  
392   0.000000e+00  
393   0.000000e+00  
1150  0.000000e+00  

[1151 rows x 4 columns]

In [161]:
model_ridge_comms, mrcom_q2, mrcom_feature_coefficients = fit_regularized_linear_model(desired_target, conv_features.columns, lasso = False, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_ridge_comms], "model_type": ["Ridge"], "features_included": ["Communication"], "alpha": [model_ridge_comms.alpha.round(4)], "q_squared": [mrcom_q2]})], ignore_index=True)

Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.695e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.349e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.040e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.764e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.518e+02, tolerance: 6.381e+01
Objective did n

Q^2: -295.10761683181215


In [162]:
directory = os.path.dirname(output_path + 'mrcom_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mrcom_feature_coefficients.to_csv(output_path + 'mrcom_feature_coefficients' + '.csv')

In [163]:
sort_by_mean_abs(display_feature_coefficients(mrcom_feature_coefficients))

Feature          Mean  \
636           max_user_sum_function_word_accommodation -3.370963e-01   
663               min_user_sum_positivity_zscore_chats  2.817942e-01   
21                                       min_num_chars -2.178483e-01   
661           average_user_sum_positivity_zscore_chats  2.155880e-01   
382                         average_user_sum_num_words -2.072888e-01   
..                                                 ...           ...   
795                stdev_user_avg_hear_lexical_per_100 -5.649384e-07   
37                        average_home_lexical_per_100 -4.948827e-07   
828               min_user_avg_anxiety_lexical_per_100 -4.319019e-07   
665    average_user_sum_positivity_zscore_conversation  4.240958e-17   
398  average_user_sum_info_exchange_zscore_conversa... -2.834392e-17   

         Lower_CI      Upper_CI  
636 -3.372564e-01 -3.369362e-01  
663  2.816639e-01  2.819245e-01  
21  -2.181608e-01 -2.175359e-01  
661  2.154923e-01  2.156837e-01  
382 -2.073885e-01 -2.071891e-01  
..            ...           ...  
795 -5.999525e-07 -5.299242e-07  
37  -5.248934e-07 -4.648720e-07  
828 -4.342019e-07 -4.296019e-07  
665  4.225876e-17  4.256041e-17  
398 -2.842161e-17 -2.826622e-17  

[1151 rows x 4 columns]

## Conversation Features + Task Features

In [164]:
convtask_features = list(task_features.columns) + list(conv_features.columns)
model_lasso_tconv, mltconv_q2, mltconv_feature_coefficients = fit_regularized_linear_model(desired_target, convtask_features, lasso = True, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_lasso_tconv], "model_type": ["Lasso"], "features_included": ["Task Complexity + Communication"], "alpha": [model_lasso_tconv.alpha.round(4)], "q_squared": [mltconv_q2]})], ignore_index=True)

Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.695e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.349e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.040e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.764e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.518e+02, tolerance: 6.381e+01
Objective did n

Q^2: -7.511795451020653e-05


In [165]:
directory = os.path.dirname(output_path + 'mltconv_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mltconv_feature_coefficients.to_csv(output_path + 'mltconv_feature_coefficients' + '.csv')

In [166]:
sort_by_mean_abs(display_feature_coefficients(mltconv_feature_coefficients))

Feature          Mean      Lower_CI      Upper_CI
702           min_user_sum_time_diff -2.996172e-06 -3.004620e-06 -2.987724e-06
315                    max_time_diff -8.659169e-07 -8.675949e-07 -8.642389e-07
783        min_user_sum_forward_flow  0.000000e+00  0.000000e+00  0.000000e+00
790     stdev_user_avg_positive_bert  0.000000e+00  0.000000e+00  0.000000e+00
789   average_user_avg_positive_bert  0.000000e+00  0.000000e+00  0.000000e+00
...                              ...           ...           ...           ...
393           max_certainty_rocklage  0.000000e+00  0.000000e+00  0.000000e+00
392           min_certainty_rocklage  0.000000e+00  0.000000e+00  0.000000e+00
391         stdev_certainty_rocklage  0.000000e+00  0.000000e+00  0.000000e+00
390       average_certainty_rocklage  0.000000e+00  0.000000e+00  0.000000e+00
1177            discursive_diversity  0.000000e+00  0.000000e+00  0.000000e+00

[1178 rows x 4 columns]

In [167]:
model_ridge_tconv, mrtconv_q2, mrtconv_feature_coefficients = fit_regularized_linear_model(desired_target, convtask_features, lasso = False, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_ridge_tconv], "model_type": ["Ridge"], "features_included": ["Task Complexity + Communication"], "alpha": [model_ridge_tconv.alpha.round(4)], "q_squared": [mrtconv_q2]})], ignore_index=True)

Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.695e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.349e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.040e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.764e+02, tolerance: 6.381e+01
Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.518e+02, tolerance: 6.381e+01
Objective did n

Q^2: -297.5522246424715


In [168]:
directory = os.path.dirname(output_path + 'mrtconv_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mrtconv_feature_coefficients.to_csv(output_path + 'mrtconv_feature_coefficients' + '.csv')

In [169]:
sort_by_mean_abs(display_feature_coefficients(mrtconv_feature_coefficients))

Feature          Mean  \
663           max_user_sum_function_word_accommodation -3.368650e-01   
690               min_user_sum_positivity_zscore_chats  2.814052e-01   
48                                       min_num_chars -2.172696e-01   
688           average_user_sum_positivity_zscore_chats  2.151866e-01   
409                         average_user_sum_num_words -2.074211e-01   
..                                                 ...           ...   
822                stdev_user_avg_hear_lexical_per_100 -4.900708e-07   
855               min_user_avg_anxiety_lexical_per_100 -4.303612e-07   
692    average_user_sum_positivity_zscore_conversation  4.224210e-17   
425  average_user_sum_info_exchange_zscore_conversa... -2.811098e-17   
23                              Q25_type6_mixed_motive  0.000000e+00   

         Lower_CI      Upper_CI  
663 -3.370250e-01 -3.367049e-01  
690  2.812750e-01  2.815354e-01  
48  -2.175819e-01 -2.169574e-01  
688  2.150911e-01  2.152822e-01  
409 -2.075207e-01 -2.073214e-01  
..            ...           ...  
822 -5.250401e-07 -4.551015e-07  
855 -4.326622e-07 -4.280602e-07  
692  4.209149e-17  4.239272e-17  
425 -2.818861e-17 -2.803335e-17  
23   0.000000e+00  0.000000e+00  

[1178 rows x 4 columns]

## Model with All Features

In [ ]:
all_features = list(task_features.columns) + list(team_composition_features.columns) + list(conv_features.columns)
model_lasso_all, mlall_q2, mlall_feature_coefficients = fit_regularized_linear_model(desired_target, all_features, lasso = True, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_lasso_all], "model_type": ["Lasso"], "features_included": ["All Features"], "alpha": [model_lasso_all.alpha.round(4)], "q_squared": [mlall_q2]})], ignore_index=True)


In [ ]:
directory = os.path.dirname(output_path + 'mlall_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mlall_feature_coefficients.to_csv(output_path + 'mlall_feature_coefficients' + '.csv')

In [ ]:
sort_by_mean_abs(display_feature_coefficients(mlall_feature_coefficients))

In [ ]:
model_ridge_all, mrall_q2, mrall_feature_coefficients = fit_regularized_linear_model(desired_target, all_features, lasso = False, tune_alpha = True)
result_df = pd.concat([result_df, pd.DataFrame({"model": [model_ridge_all], "model_type": ["Ridge"], "features_included": ["All Features"], "alpha": [model_ridge_all.alpha.round(4)], "q_squared": [mrall_q2]})], ignore_index=True)

In [ ]:
directory = os.path.dirname(output_path + 'mrall_feature_coefficients' + '.csv')
if not os.path.exists(directory):
    os.makedirs(directory)
mrall_feature_coefficients.to_csv(output_path + 'mrall_feature_coefficients' + '.csv')

In [ ]:
sort_by_mean_abs(display_feature_coefficients(mrall_feature_coefficients))

# Dataframe that summarizes all these experiments!

In [ ]:
result_df.sort_values(by = "q_squared", ascending = False)

In [ ]:
# Save for comparing results
directory = os.path.dirname(validation_results_output_name)
if not os.path.exists(directory):
    os.makedirs(directory)
result_df.sort_values(by = "q_squared", ascending = False).to_csv(validation_results_output_name)

# Feature Importance

In [ ]:
sort_by_mean_abs(display_feature_coefficients(mlall_feature_coefficients))

In [ ]:
def plot_top_n_features(data, n, filepath):
    # Calculate the absolute mean value and sort the DataFrame in descending order
    data['Absolute_Mean'] = data['Mean'].abs()
    top_n_features = data.sort_values(by='Absolute_Mean', ascending=False).head(n)

    # Define color mapping for the features
    color_map = {}
    name_map = {}
    for feature in task_features.columns:
        color_map[feature] = 'yellowgreen'
        name_map[feature] = "Task Feature"
    for feature in conv_features.columns:
        color_map[feature] = 'powderblue'
        name_map[feature] = "Conversation Feature"
    for feature in team_composition_features.columns:
        color_map[feature] = 'lightpink'
        name_map[feature] = "Team Composition Feature"

    # Create a horizontal bar graph
    plt.figure(figsize=(10, 6))

    handles = []

    for feature in top_n_features['Feature']:
        color = color_map.get(feature, 'k')  # Default to black if not in any list
        bars = plt.barh(feature, top_n_features[top_n_features['Feature'] == feature]['Mean'], color=color)
        handles.append(bars[0])

    # Customize the plot
    plt.xlabel('Mean Coefficient (Across LOO Cross Validation)', fontsize = 14)
    plt.title(f'Top {n} features for {desired_target} (min chats = {min_num_chats})', fontsize=20)
    plt.gca().invert_yaxis()  # Invert the y-axis to display the highest value at the top

    plt.xticks(fontsize=14)
    plt.yticks(fontsize=14)

    # Create a legend outside the plot area with unique labels
    unique_features = []
    unique_labels = []
    for feature in top_n_features['Feature']:
        if name_map.get(feature, feature) not in unique_labels:
            unique_labels.append(name_map.get(feature, feature))
            unique_features.append(feature)

    legend_handles = [plt.Line2D([0], [0], color=color_map.get(feature, 'k'), lw=4, label=name_map.get(feature, feature)) for feature in unique_features]
    plt.legend(handles=legend_handles, loc='center left', fontsize = 14, bbox_to_anchor=(1, 0.5))

    # Add labels to the bars with increased text size and Mean rounded to 2 decimals, consistently inside the bar
    label_offset = 0.4  # Adjust this value for proper spacing
    for bar, value, feature in zip(handles, top_n_features['Mean'], top_n_features['Feature']):
        label_x = (max(value, 0) if value >= 0 else min(value, 0))
        bbox = bar.get_bbox()
        label_y = bbox.bounds[1] + label_offset
        if value >= 0:
            plt.text(label_x, label_y, f'{value:.2f}', va='center', fontsize=12)
        else:
            plt.text(label_x, label_y, f'{value:.2f}', ha='right', va='center', fontsize=12)

    # Show the plot
    plt.savefig(filepath + ".svg")
    plt.savefig(filepath + ".png")
    plt.show()

In [ ]:
plot_top_n_features(display_feature_coefficients(mlall_feature_coefficients), 10, filepath = "./figures/multi_task_cumulative_stage" + "_" + desired_target + "_min_chat_num_" + str(min_num_chats))

Questions:
- More deeply understand difference between LASSO and Ridge
- Better understand `alpha` hyperparameter
- Why doesn't more features mean a better R^2? (Wouldn't the model 'throw out' features that don't work?)